# Read and display UW-Madison HSRL L1B scanning data

## Preparing your python environment to run this jupyter notebook

## Introduction

The ground-based University of Wisconsin (UW)-Madison scanning High Spectral Resolution Lidar (HSRL) *L1B* (similar to a NASA CALIOP L1B product) scanning product consists of the following geophysical 532nm wavelength calibrated measurements:
1. particulate backscatter [$\mathrm{m}^{-1}\,\mathrm{sr}^{-1}$],
2. particulate linear depolarization ratio,
3. particulate optical depth,
4. and attenuated color ratio between the 1064nm and 532nm wavelengths. 

The calibrated 1064nm attenuated backscatter [$\mathrm{m}^{-1}\,\mathrm{sr}^{-1}$] will be added in the future, along with uncertainties (i.e. standard deviation) of each geophysical variable. 

The UW HSRL produces these measurements in three viewing configurations. Similar to most ground-based lidar instruments the UW HSRL make continuous "up looking" measurements which we call **vertical stare** measurements. Next, the UW HSRL is capable of making continuous **horizontal stare** measurements at an oblique angle between 70° and 90° relative to zenith. Finally, the HSRL makes repeated **scanning** measurements between 70° and 90°, nominally in 0.5° steps, where each directional scan is conducted within a minute.

These three viewing measurement configurations are organized in their own netcdf4 groups which will be discussed in the subsequent subsections. Here is how you download the sample (prelimary) 1.4 GB L1B netcdf4 file.

In [1]:
import urllib.request
from pathlib import Path

# The remote URL of the sample L1B file
remote_l1b_url_str = (
    "https://ftp.ssec.wisc.edu/pub/incoming/"
    "bagohsrl_20230814T000000_20230815T000000_30.0s_7.5m_1.0deg_L1B_preliminary.nc"
)

# Whereto the file will be loaded
l1b_fileP = Path("~/").expanduser() / Path(remote_l1b_url_str).name

# If the file has not been downloaded yet...download the file
if l1b_fileP.exists() is False:
    _, header_obj = urllib.request.urlretrieve(remote_l1b_url_str, str(l1b_fileP))

    # Print how big the file is that you downloaded, just to 
    # make sure that the whole 1.4 GB of data was downloaded
    print(
        "Downloaded {:.1f} GB of data to file {:s}.".format(
            round(int(header_obj["Content-Length"]) / 1024**3, 1),
            str(l1b_fileP)
        )
    )

## The file name convention

The L1B file name consists of the following parts:
```
<instrument name>_<start date>_<end date>_<time resolution>s_<altitude resolution>m_<angle resolution>deg_L1B<_tag>.nc
```
For example the specific UW HSRL instrument is designated as the `bagohsrl`. The file consists of measurements of the 4th of August where the nominal time and altitude resolutions are 30 seconds and 7.5 meters, and the scanning data has a (downsampled) angular resolution of 1 degree. Finally the tag `preliminary` provides a label of the file.

## Geophysical variable naming convention

Similar to the CALIOP L1B product the geophysical variable names encode the wavelength. The self explanatory variable names are 

* `particulate_backscatter_532nm`
* `particulate_linear_depolarization_532nm`
* `particulate_optical_depth_532nm`
* `attenuated_color_ratio_1064nm_532nm`

## Vertical stare measurements

Here is how you get the vertical stare data via xarray. The HSRL geophysical variable dimensions are time and mean sea level (MSL) altitude. When you hover your mouse cursor over the variable name under `Data variables` you will see the full name. The document icon button to the far right, when clicked upon, shows you the attributes of the corresponding variable. 

In [2]:
import xarray as xr

vert_stare_ds = xr.open_dataset(l1b_fileP, group="vertical_stare")
vert_stare_ds

<xarray.Dataset>
Dimensions:                                  (time: 2880, altitude: 2668)
Coordinates:
  * time                                     (time) datetime64[ns] 2023-08-14...
  * altitude                                 (altitude) float64 7.223 ... 1.9...
Data variables:
    particulate_linear_depolarization_532nm  (time, altitude) float64 ...
    optical_depth_532nm                      (time, altitude) float64 ...
    particulate_optical_depth_532nm          (time, altitude) float64 ...
    particulate_backscatter_532nm            (time, altitude) float64 ...
    attenuated_color_ratio_1064nm_532nm      (time, altitude) float64 ...
Attributes:
    documentation:  github.com/ssec/hsrl

Here is how you plot the geophysical variables with hvplot / holoviews / bokeh.

In [3]:
import hvplot.xarray
import holoviews as hv

hv.extension("bokeh")
hv.config.image_rtol = 10
hv.opts.defaults(hv.opts.Image(active_tools=["box_zoom"]))
hv.opts.defaults(hv.opts.QuadMesh(active_tools=["box_zoom"]))
hv.opts.defaults(hv.opts.Curve(active_tools=["box_zoom"], show_grid=True))

# TODO
enable_plot_rasterize_bl = True

(
    # Plot the particulate backscatter
    vert_stare_ds.particulate_backscatter_532nm.hvplot(
        x="time", y="altitude", cmap="turbo", clim=(1e-8, 1e-4), logz=True,
        clabel="{:s} [:s]".format(
            vert_stare_ds.particulate_backscatter_532nm.attrs["long_name"],
            vert_stare_ds.particulate_backscatter_532nm.attrs["units"]
        ),
        rasterize=enable_plot_rasterize_bl
    ).opts(title=vert_stare_ds.particulate_backscatter_532nm.attrs["long_name"].replace("_", " "))
    
    # Plot the particulate linear depolarization
    + vert_stare_ds.particulate_linear_depolarization_532nm.hvplot(
        x="time", y="altitude", cmap="turbo", clim=(0, 0.6),
        clabel="{:s}".format(
            vert_stare_ds.particulate_linear_depolarization_532nm.attrs["long_name"],
        ),
        rasterize=enable_plot_rasterize_bl
    ).opts(title=vert_stare_ds.particulate_linear_depolarization_532nm.attrs["long_name"].replace("_", " "))
    
    # Plot the particulate optical depth
    + vert_stare_ds.particulate_optical_depth_532nm.hvplot(
        x="time", y="altitude", cmap="turbo", clim=(None, 0.8),
        clabel="{:s}".format(
            vert_stare_ds.particulate_optical_depth_532nm.attrs["long_name"],
        ),
        rasterize=enable_plot_rasterize_bl
    ).opts(title=vert_stare_ds.particulate_optical_depth_532nm.attrs["long_name"].replace("_", " "))
    
    # Plot the attenuated color ratio
    + vert_stare_ds.attenuated_color_ratio_1064nm_532nm.hvplot(
        x="time", y="altitude", cmap="turbo", clim=(0, 1.0),
        clabel="{:s}".format(
            vert_stare_ds.attenuated_color_ratio_1064nm_532nm.attrs["long_name"],
        ),
        rasterize=enable_plot_rasterize_bl
    ).opts(title=vert_stare_ds.attenuated_color_ratio_1064nm_532nm.attrs["long_name"].replace("_", " "))
).opts(title="MAGPIE, Barbados, Ragged Point, 2023-08-14").cols(2)

OMP: Info #276: omp_set_nested routine deprecated, please use omp_set_max_active_levels instead.


:Layout
   .DynamicMap.I   :DynamicMap   []
      :Image   [time,altitude]   (particulate_backscatter_532nm)
   .DynamicMap.II  :DynamicMap   []
      :Image   [time,altitude]   (particulate_linear_depolarization_532nm)
   .DynamicMap.III :DynamicMap   []
      :Image   [time,altitude]   (particulate_optical_depth_532nm)
   .DynamicMap.IV  :DynamicMap   []
      :Image   [time,altitude]   (attenuated_color_ratio_1064nm_532nm)

## Horizontal stare measurements

## Scanning measurements